In [1]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.datasets import cifar10
from tensorflow.keras.layers import Input, Dense, Reshape, Flatten, Dropout
from tensorflow.keras.layers import BatchNormalization, Activation, ZeroPadding2D
from tensorflow.python.keras.layers.advanced_activations import LeakyReLU 
from tensorflow.python.keras.layers.convolutional import UpSampling2D, Conv2D
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.regularizers import l2
from tensorflow.keras.optimizers import Adam
import matplotlib.pyplot as plt
import sys
import numpy as np

C:\Users\ragja\Anaconda3\envs\test\lib\site-packages\tensorflow\python\framework\dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\ragja\Anaconda3\envs\test\lib\site-packages\tensorflow\python\framework\dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\ragja\Anaconda3\envs\test\lib\site-packages\tensorflow\python\framework\dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\ragja\Anaconda3\envs\test\lib\site-packages\tensorflow\python\frame

In [2]:
class GAN():
    def __init__(self):
        self.N = 60000
        self.img_rows = 32
        self.img_cols = 32
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100
        self.dropout = 0.6
        lengthscale = 1e-2
        self.reg = lengthscale**2 * (1 - self.dropout) / (2. * self.N )
        
        optimizer = Adam(0.0002, 0.5)
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
        self.generator = self.build_generator()

        z = Input(shape=(self.latent_dim,))
        img = self.generator(z)
        print(img.shape)

        self.discriminator.trainable = False
        validity = self.discriminator(img)
        self.combined = Model(z, validity)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)
        
    def build_generator(self):
        noise = Input(shape=(self.latent_dim,))
        model = Dense(128 * 8 * 8, activation="relu", input_dim=self.latent_dim, kernel_regularizer=l2(self.reg))(noise)
        model = Dropout(0.6)(model,training=True)
        model = Reshape((8, 8, 128))(model)
        model = UpSampling2D(size=(2, 2))(model)
        model = Conv2D(128, kernel_size=3, padding="same", activation="relu", kernel_regularizer=l2(self.reg))(model)
        model = BatchNormalization(momentum=0.8)(model)
        model = UpSampling2D(size=(2, 2))(model)
        model = Conv2D(64, kernel_size=3, padding="same", activation="relu", kernel_regularizer=l2(self.reg))(model)
        model = BatchNormalization(momentum=0.8)(model)
        #model = Dropout(0.25)(model,training=True)
        output = Conv2D(self.channels, kernel_size=3, padding="same", activation="tanh", kernel_regularizer=l2(self.reg))(model)        
        return Model(noise, output)
    
    def build_discriminator(self):
        img = Input(shape=self.img_shape)
        model = Conv2D(64, kernel_size=5, strides=2, input_shape=self.img_shape, padding="same", kernel_regularizer=l2(self.reg))(img)
        model = LeakyReLU(alpha=0.2)(model)
        model = Dropout(0.25)(model)
        model = Conv2D(128, kernel_size=5, strides=2, padding="same", kernel_regularizer=l2(self.reg))(model)
        model = ZeroPadding2D(padding=((0, 1), (0, 1)))(model)
        model = BatchNormalization(momentum=0.8)(model)
        model = LeakyReLU(alpha=0.2)(model)
        model = Dropout(0.25)(model,training=True)
        model = Conv2D(256, kernel_size=5, strides=2, padding="same", kernel_regularizer=l2(self.reg))(model)
        model = BatchNormalization(momentum=0.8)(model)
        model = LeakyReLU(alpha=0.2)(model)
        model = Dropout(0.25)(model,training=True)
        model = Conv2D(512, kernel_size=5, strides=1, padding="same", kernel_regularizer=l2(self.reg))(model)
        model = BatchNormalization(momentum=0.8)(model)
        model = LeakyReLU(alpha=0.2)(model)
        model = Dropout(0.25)(model,training=True)
        model = Flatten()(model)
        output = Dense(1, activation='sigmoid')(model)     
        return Model(img, output)
    
    def train(self, epochs, batch_size=128, sample_interval=50):
        (X_train, _), (_, _) = cifar10.load_data()
        X_train = X_train / 127.5 - 1.
        #X_train = np.expand_dims(X_train, axis=3)
        valid = np.ones((batch_size, 1))
        fake = np.zeros((batch_size, 1))
        for epoch in range(epochs):
            idx = np.random.randint(0, X_train.shape[0], batch_size)
            imgs = X_train[idx]
            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
            gen_imgs = self.generator.predict(noise)
            d_loss_real = self.discriminator.train_on_batch(imgs, valid)
            d_loss_fake = self.discriminator.train_on_batch(gen_imgs, fake)
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)
            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
            g_loss = self.combined.train_on_batch(noise, valid)
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))
            if epoch % sample_interval == 0:
               self.sample_images(epoch)
            
    def sample_images(self, epoch):
        r, c = 5, 5
        noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        gen_imgs = self.generator.predict(noise)
        gen_imgs = 0.5 * gen_imgs + 0.5
        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt, :,:,:])
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("images/%d.png" % epoch)
        plt.close()
    
    def predict(self, no_samples):
        r, c = 5, 5
        noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        for k in range(no_samples):
            
            gen_imgs = self.generator.predict(noise)
            gen_imgs = 0.5 * gen_imgs + 0.5
            fig, axs = plt.subplots(r, c)
            cnt = 0
            for i in range(r):
                for j in range(c):
                    axs[i,j].imshow(gen_imgs[cnt, :,:,:])
                    axs[i,j].axis('off')
                    cnt += 1
            fig.savefig("images/%d.png" % k)
            plt.close()

In [3]:
gan = GAN()
gan.train(epochs=28000, batch_size=128, sample_interval=1000)

(?, 32, 32, 3)
0 [D loss: 4.519145, acc.: 27.73%] [G loss: 0.117515]
1 [D loss: 1.074486, acc.: 51.95%] [G loss: 7.460690]
2 [D loss: 2.932215, acc.: 50.00%] [G loss: 2.989533]
3 [D loss: 1.054491, acc.: 48.83%] [G loss: 0.740570]
4 [D loss: 0.064399, acc.: 98.83%] [G loss: 0.737788]
5 [D loss: 0.046084, acc.: 98.83%] [G loss: 0.273383]
6 [D loss: 0.029061, acc.: 99.22%] [G loss: 0.086219]
7 [D loss: 0.005303, acc.: 100.00%] [G loss: 0.052949]
8 [D loss: 0.003411, acc.: 100.00%] [G loss: 0.025289]
9 [D loss: 0.002523, acc.: 100.00%] [G loss: 0.035847]
10 [D loss: 0.002414, acc.: 100.00%] [G loss: 0.012529]
11 [D loss: 0.004131, acc.: 100.00%] [G loss: 0.018754]
12 [D loss: 0.009209, acc.: 100.00%] [G loss: 0.035135]
13 [D loss: 0.009086, acc.: 100.00%] [G loss: 0.042592]
14 [D loss: 0.010981, acc.: 100.00%] [G loss: 0.048381]
15 [D loss: 0.015600, acc.: 100.00%] [G loss: 0.113133]
16 [D loss: 0.019561, acc.: 100.00%] [G loss: 0.306840]
17 [D loss: 0.022962, acc.: 100.00%] [G loss: 0.46

21 [D loss: 2.024765, acc.: 48.44%] [G loss: 6.528909]
22 [D loss: 0.990881, acc.: 68.36%] [G loss: 1.678825]
23 [D loss: 0.795667, acc.: 69.53%] [G loss: 4.263046]
24 [D loss: 0.291056, acc.: 90.23%] [G loss: 2.616161]
25 [D loss: 1.198496, acc.: 57.42%] [G loss: 11.445894]
26 [D loss: 2.337306, acc.: 49.22%] [G loss: 3.623168]
27 [D loss: 2.608984, acc.: 40.62%] [G loss: 7.800590]
28 [D loss: 1.833198, acc.: 49.61%] [G loss: 5.384603]
29 [D loss: 1.528637, acc.: 42.97%] [G loss: 3.085419]
30 [D loss: 0.591512, acc.: 72.27%] [G loss: 3.191890]
31 [D loss: 0.631109, acc.: 71.48%] [G loss: 1.824492]
32 [D loss: 0.687084, acc.: 67.97%] [G loss: 2.259200]
33 [D loss: 0.645079, acc.: 70.70%] [G loss: 2.403001]
34 [D loss: 1.458919, acc.: 41.02%] [G loss: 2.565486]
35 [D loss: 0.610383, acc.: 71.88%] [G loss: 3.246615]
36 [D loss: 1.109962, acc.: 55.08%] [G loss: 3.048541]
37 [D loss: 1.182629, acc.: 45.70%] [G loss: 3.175748]
38 [D loss: 0.923284, acc.: 57.81%] [G loss: 3.032451]
39 [D los

43 [D loss: 0.855423, acc.: 57.81%] [G loss: 3.183614]
44 [D loss: 0.796940, acc.: 62.89%] [G loss: 3.300774]
45 [D loss: 0.576937, acc.: 77.73%] [G loss: 3.580854]
46 [D loss: 0.737835, acc.: 60.55%] [G loss: 2.375165]
47 [D loss: 0.413545, acc.: 78.52%] [G loss: 3.697227]
48 [D loss: 0.580195, acc.: 68.75%] [G loss: 2.705750]
49 [D loss: 0.413121, acc.: 80.47%] [G loss: 3.199097]
50 [D loss: 0.845949, acc.: 60.55%] [G loss: 3.120879]
51 [D loss: 0.346696, acc.: 85.16%] [G loss: 3.404690]
52 [D loss: 0.878941, acc.: 53.12%] [G loss: 5.726255]
53 [D loss: 1.116659, acc.: 53.52%] [G loss: 2.180230]
54 [D loss: 0.380135, acc.: 83.98%] [G loss: 4.502261]
55 [D loss: 0.360837, acc.: 82.42%] [G loss: 3.633453]
56 [D loss: 0.632621, acc.: 65.62%] [G loss: 4.032009]
57 [D loss: 0.270552, acc.: 91.80%] [G loss: 4.850492]
58 [D loss: 0.929062, acc.: 53.91%] [G loss: 5.522504]
59 [D loss: 0.610076, acc.: 72.66%] [G loss: 3.203660]
60 [D loss: 0.364175, acc.: 84.38%] [G loss: 3.862859]
61 [D loss

65 [D loss: 0.301137, acc.: 87.89%] [G loss: 2.791297]
66 [D loss: 0.823582, acc.: 57.81%] [G loss: 6.243956]
67 [D loss: 2.723361, acc.: 8.98%] [G loss: 2.248495]
68 [D loss: 0.771888, acc.: 65.23%] [G loss: 2.771338]
69 [D loss: 0.836037, acc.: 57.81%] [G loss: 3.147613]
70 [D loss: 0.898210, acc.: 53.12%] [G loss: 2.593042]
71 [D loss: 0.444454, acc.: 77.34%] [G loss: 3.100739]
72 [D loss: 0.296070, acc.: 89.06%] [G loss: 3.811664]
73 [D loss: 0.495076, acc.: 78.12%] [G loss: 3.123309]
74 [D loss: 0.315385, acc.: 87.11%] [G loss: 3.027097]
75 [D loss: 0.488612, acc.: 75.39%] [G loss: 3.470488]
76 [D loss: 0.403577, acc.: 83.59%] [G loss: 2.922519]
77 [D loss: 1.611982, acc.: 24.61%] [G loss: 3.529740]
78 [D loss: 0.493108, acc.: 77.34%] [G loss: 2.992979]
79 [D loss: 0.390871, acc.: 84.38%] [G loss: 2.698209]
80 [D loss: 0.471359, acc.: 77.34%] [G loss: 3.576597]
81 [D loss: 0.445920, acc.: 78.91%] [G loss: 2.962828]
82 [D loss: 0.215616, acc.: 91.41%] [G loss: 3.939340]
83 [D loss:

87 [D loss: 0.654526, acc.: 71.09%] [G loss: 1.148308]
88 [D loss: 0.394668, acc.: 83.59%] [G loss: 3.483967]
89 [D loss: 0.425280, acc.: 85.94%] [G loss: 1.588263]
90 [D loss: 0.521026, acc.: 74.22%] [G loss: 8.114674]
91 [D loss: 2.125569, acc.: 22.27%] [G loss: 2.392592]
92 [D loss: 0.288866, acc.: 86.33%] [G loss: 4.925957]
93 [D loss: 0.432168, acc.: 83.20%] [G loss: 3.250813]
94 [D loss: 0.289880, acc.: 88.28%] [G loss: 3.966979]
95 [D loss: 0.187987, acc.: 94.92%] [G loss: 3.212440]
96 [D loss: 0.196701, acc.: 94.92%] [G loss: 3.191527]
97 [D loss: 0.141459, acc.: 98.44%] [G loss: 3.752285]
98 [D loss: 0.310133, acc.: 86.72%] [G loss: 3.482304]
99 [D loss: 0.239690, acc.: 91.02%] [G loss: 4.084546]
100 [D loss: 0.141647, acc.: 94.92%] [G loss: 3.796612]
101 [D loss: 0.068058, acc.: 99.22%] [G loss: 4.069245]
102 [D loss: 0.056094, acc.: 98.44%] [G loss: 4.079136]
103 [D loss: 0.046876, acc.: 99.61%] [G loss: 4.255912]
104 [D loss: 0.049164, acc.: 100.00%] [G loss: 5.277502]
105 

...

22439 [D loss: 0.570174, acc.: 72.66%] [G loss: 2.275354]
22440 [D loss: 0.148208, acc.: 94.14%] [G loss: 7.934110]
22441 [D loss: 0.019713, acc.: 99.61%] [G loss: 8.583446]
22442 [D loss: 0.023160, acc.: 100.00%] [G loss: 6.856296]
22443 [D loss: 0.024154, acc.: 100.00%] [G loss: 4.354204]
22444 [D loss: 0.027305, acc.: 99.22%] [G loss: 5.160651]
22445 [D loss: 0.077095, acc.: 98.83%] [G loss: 5.559115]
22446 [D loss: 0.069349, acc.: 99.22%] [G loss: 3.796326]
22447 [D loss: 0.075878, acc.: 98.44%] [G loss: 6.955677]
22448 [D loss: 0.055290, acc.: 97.66%] [G loss: 5.111023]
22449 [D loss: 1.677634, acc.: 35.16%] [G loss: 10.836402]
22450 [D loss: 0.229659, acc.: 87.89%] [G loss: 8.894590]
22451 [D loss: 0.115705, acc.: 95.31%] [G loss: 7.304251]
22452 [D loss: 0.184148, acc.: 93.75%] [G loss: 2.943718]
22453 [D loss: 0.048406, acc.: 99.22%] [G loss: 5.928647]
22454 [D loss: 0.254038, acc.: 89.06%] [G loss: 4.820886]
22455 [D loss: 0.179887, acc.: 92.58%] [G loss: 7.794602]
22456 [D lo

22461 [D loss: 0.104985, acc.: 96.88%] [G loss: 5.881794]
22462 [D loss: 0.017220, acc.: 100.00%] [G loss: 5.394098]
22463 [D loss: 0.056222, acc.: 98.83%] [G loss: 2.942877]
22464 [D loss: 0.266579, acc.: 90.62%] [G loss: 8.462003]
22465 [D loss: 0.044608, acc.: 98.83%] [G loss: 11.705912]
22466 [D loss: 0.058693, acc.: 98.44%] [G loss: 7.775098]
22467 [D loss: 0.018186, acc.: 100.00%] [G loss: 6.748713]
22468 [D loss: 0.075800, acc.: 98.83%] [G loss: 6.452642]
22469 [D loss: 0.025296, acc.: 99.61%] [G loss: 4.926672]
22470 [D loss: 0.052343, acc.: 98.83%] [G loss: 5.522897]
22471 [D loss: 0.060403, acc.: 98.83%] [G loss: 6.383345]
22472 [D loss: 0.643085, acc.: 67.97%] [G loss: 7.665117]
22473 [D loss: 0.094683, acc.: 96.09%] [G loss: 11.488744]
22474 [D loss: 0.797662, acc.: 63.67%] [G loss: 2.048882]
22475 [D loss: 1.007287, acc.: 58.20%] [G loss: 10.045621]
22476 [D loss: 0.425132, acc.: 75.39%] [G loss: 6.975193]
22477 [D loss: 0.017407, acc.: 100.00%] [G loss: 3.578996]
22478 [D

22483 [D loss: 0.005470, acc.: 100.00%] [G loss: 5.652417]
22484 [D loss: 0.049311, acc.: 100.00%] [G loss: 5.994342]
22485 [D loss: 0.024473, acc.: 100.00%] [G loss: 7.939108]
22486 [D loss: 0.049881, acc.: 99.22%] [G loss: 7.635867]
22487 [D loss: 0.163379, acc.: 94.92%] [G loss: 6.111197]
22488 [D loss: 0.058010, acc.: 99.22%] [G loss: 8.460579]
22489 [D loss: 0.116471, acc.: 96.88%] [G loss: 3.751148]
22490 [D loss: 0.059893, acc.: 98.83%] [G loss: 5.968771]
22491 [D loss: 0.006045, acc.: 100.00%] [G loss: 4.754533]
22492 [D loss: 0.036872, acc.: 99.61%] [G loss: 5.818937]
22493 [D loss: 0.018537, acc.: 99.61%] [G loss: 5.347220]
22494 [D loss: 0.018579, acc.: 100.00%] [G loss: 4.988275]
22495 [D loss: 0.003740, acc.: 100.00%] [G loss: 6.018405]
22496 [D loss: 0.013680, acc.: 100.00%] [G loss: 5.092921]
22497 [D loss: 0.025350, acc.: 99.61%] [G loss: 6.139386]
22498 [D loss: 0.006785, acc.: 100.00%] [G loss: 5.711404]
22499 [D loss: 0.010097, acc.: 100.00%] [G loss: 7.391903]
22500

22505 [D loss: 0.136319, acc.: 96.88%] [G loss: 6.879163]
22506 [D loss: 0.028619, acc.: 99.22%] [G loss: 3.912166]
22507 [D loss: 0.036168, acc.: 98.83%] [G loss: 4.559972]
22508 [D loss: 0.127342, acc.: 97.66%] [G loss: 5.848121]
22509 [D loss: 0.083763, acc.: 97.66%] [G loss: 5.874640]
22510 [D loss: 0.213765, acc.: 93.36%] [G loss: 3.509442]
22511 [D loss: 0.035483, acc.: 99.22%] [G loss: 4.219232]
22512 [D loss: 0.015074, acc.: 99.61%] [G loss: 5.808879]
22513 [D loss: 0.038013, acc.: 99.22%] [G loss: 6.700465]
22514 [D loss: 0.034104, acc.: 99.22%] [G loss: 5.981842]
22515 [D loss: 0.110729, acc.: 97.66%] [G loss: 5.359368]
22516 [D loss: 0.014327, acc.: 100.00%] [G loss: 3.622251]


KeyboardInterrupt: 

In [4]:
gan.predict(5)